# Prepare Dispersal syndrome data from TRY for use

The Dispersal syndrome data from TRY informs on whether plant seeds spread through water, animals, rainfall, wind, humans or unassisted.

*If you intend to clean more than one or two traits, we recommend the use of the batch pre-processing script. Refer to the [TRY main page](try-label) for details.*
 
If you have questions, suggestions, spot errors, or want to contribute, get in touch with us through planthub@idiv.de.

Author: David Schellenberger Costa

## Requirements

To run the script, the following is needed:
- TRY data, available <a href="https://planthub.idiv.de/downloads/" target="_parent">here</a>
- the data.table library may need to be installed

## Code

In [ ]:
# load in libraries
library(data.table) # handle large datasets

# clear workspace
rm(list = ls())


Let's get the TRY data.

In [ ]:
# set working directory (adapt this!)
setwd(paste0(.brd, "PlantHub"))

# read in data (adapt this!)
TRY <- fread("TRY_PlantHub.gz")

# select data of interest
TRYSubset <- TRY[TraitName == "Dispersal syndrome"]


To get an overview of the data, we convert values to lowercase, sort them, and show them as
a table.

In [ ]:
# extract original data strings
oriVals <- TRYSubset$OrigValueStr # oriVals == original values

# change all to lowercase to ease later classification
oriVals <- tolower(oriVals)

# get an overview over the data by summarizing values and showing them in alphabetical order
valueOverview <- table(oriVals)
valueOverview[order(valueOverview)]


Some entries are just a few characters. This is likely a coding that should be decoded.

In [ ]:
# decode coded entries
strsplit(TRYSubset[DatasetID == 474]$Comment[1], split = ";|,")
codes <- c("G", "W", "H", "B", "M", "N", "P", "O", "Z")
repls <- c("baro", "anemo", "hydro", "ballisto", "myrmeco", "endozoo", "epizoo", "zoo", "zoo")
oriVals[TRYSubset$DatasetID == 474] <- toupper(oriVals[TRYSubset$DatasetID == 474])
for (i in seq_along(codes)) {
	oriVals[TRYSubset$DatasetID == 474] <-
		gsub(codes[i], paste0(" ", repls[i], "chor "), oriVals[TRYSubset$DatasetID == 474])
}
oriVals[TRYSubset$DatasetID == 319 & TRYSubset$OrigValueStr == "yes"] <-
	TRYSubset[DatasetID == 319 & OrigValueStr == "yes"]$OriglName
oriVals[TRYSubset$DatasetID == 351 & TRYSubset$OrigValueStr == "1"] <-
	TRYSubset[DatasetID == 351 & OrigValueStr == "1"]$OriglName
oriVals[TRYSubset$DatasetID == 435 & TRYSubset$OrigValueStr == "1"] <-
	TRYSubset[DatasetID == 435 & OrigValueStr == "1"]$OriglName


It looks like a good idea to remove purely numeric values.

In [ ]:
oriVals[!grepl("[[:lower:]]", oriVals)] <- NA


The most important part of the cleaning process is the definition of the search strings to look for.
We use regular expressions in some cases to be more inclusive (or exclusive).

In [ ]:
searchNames <- c(
	"herpochor|tumbling|dispersal no|autochor|unassisted|unspecialised|drop to the ground|unspecialised|baro|gravity", # nolint: line_length_linter.
	"^ane$|meteorochor|wind|anemo|boleochor|chamaechor|semachor",
	"eaten|endo-?zoochor|^endo?$",
	"(ecto|epi)-?zoochor|adhesion|^epi$",
	"dysochor|hoarding|squirrel|shrew",
	"(^|[^A-Za-z])ant|myrme(co)?chor",
	"nautochor|water|hydrochor|bythisochor|floating",
	"ballochor|ballistochor|explosive|blastochor|ballistic",
	"([^Aa]|^)biotic|zoochor|grouse|animal|cattle|ox|sheep|bird|deer|horse|pig|rabbit|ma(m)?mal|mouse|goat|hare|donkey|vertebrate|ornithochor|chamois|marten|pacarana|boar|roe|fox|dog|snail|earthworm|badger|trichoptera|monkey|marmot|reptile|fish|civet|beetle|chimpanzee|bat|turtle", # nolint: line_length_linter.
	"(^man)|agochor|human|ethelochor|commerce|vehicle|speirochor|machine|footwear|hemerochor",
	"ombrochor|rain"
)


We can now search for the strings defined before and give names to the new categories.

In [ ]:
# search for the strings defined before
searchResults <- sapply(searchNames, grepl, oriVals, ignore.case = TRUE)

# name columns of searchResults matrix like corrected searchNames
colnames(searchResults) <- c(
	"autochorous", "anemochorous", "endozoochorous", "epizoochorous", "dysochorous", "myrmechorous",
	"hydrochorous", "ballochorous", "zoochorous", "anthropochorous", "ombrochorous"
)


Let's have a look at the results.

In [ ]:
# show the number of matches to each category
colSums(searchResults)

# show the original entries for which no match was retrieved
oriVals[rowSums(searchResults) < 1]

# show the number of entries that weren't matched to any category
sum(rowSums(searchResults) < 1)

# show the number of entries that were matched to more that one category
sum(rowSums(searchResults) > 1)


As myrmechory and epi-/ecto-/endo-zoochory are all types of zoochory, we should make sure this term is also found in the new value strings whenever a sub-category of zoochory is mentioned.

In [ ]:
# consider logical relationships
# myrmechory, epizoochory, and endozoochory are all zoochory
searchResults[
	rowSums(searchResults[, grep("zoo|myrme|dyso", colnames(searchResults))]) > 0,
	grep("^zoo", colnames(searchResults))
] <- TRUE


Now, we can create new strings with the cleaned values and add them to the observations. To
not remove the original entries, we will create a new column called "CleanedValueStr".

In [ ]:
# use the searchResults matrix to create new value strings by concatenating all data found
newVals <- sapply(seq_len(nrow(searchResults)), function(x) {
	paste(colnames(searchResults)[searchResults[x, ]], collapse = ",")
})
newVals[newVals == ""] <- NA

# integrate into TRY
TRY[TraitName == "Dispersal syndrome", CleanedValueStr := newVals]


Although not necessary, we may change the trait name.

In [ ]:
TRY[TraitName == "Dispersal syndrome", TraitName := "Plant dispersal syndrome"]


Let's write the data to a file.

In [ ]:
fwrite(TRY, file = paste0("TRY_processed_", Sys.Date(), ".gz"))
